In [1]:
import numpy as np
import pandas as pd

In [2]:
xlsx=pd.ExcelFile("data/Brazilian Immigrants - typo fixed.xlsx")
# state_code=pd.read_excel(xlsx,'State code',index_col='FIPS Code')
state_code=pd.read_excel(xlsx,'State code')
state_code.head()

State Abbreviation  FIPS Code  State Name
0                 AL          1     ALABAMA
1                 AK          2      ALASKA
2                 AZ          4     ARIZONA
3                 AR          5    ARKANSAS
4                 CA          6  CALIFORNIA

In [3]:
column_name = pd.Series(state_code['State Abbreviation'].values, index=state_code['FIPS Code'])
column_dict=column_name.to_dict()
# print(column_name)
print(column_dict)

{1: 'AL', 2: 'AK', 4: 'AZ', 5: 'AR', 6: 'CA', 8: 'CO', 9: 'CT', 10: 'DE', 11: 'DC', 12: 'FL', 13: 'GA', 15: 'HI', 16: 'ID', 17: 'IL', 18: 'IN', 19: 'IA', 20: 'KS', 21: 'KY', 22: 'LA', 23: 'ME', 24: 'MD', 25: 'MA', 26: 'MI', 27: 'MN', 28: 'MS', 29: 'MO', 30: 'MT', 31: 'NE', 32: 'NV', 33: 'NH', 34: 'NJ', 35: 'NM', 36: 'NY', 37: 'NC', 38: 'ND', 39: 'OH', 40: 'OK', 41: 'OR', 42: 'PA', 44: 'RI', 45: 'SC', 46: 'SD', 47: 'TN', 48: 'TX', 49: 'UT', 50: 'VT', 51: 'VA', 53: 'WA', 54: 'WV', 55: 'WI', 56: 'WY', 72: 'PR', 78: 'VI'}


In [4]:
def read_year(year:str):
    xlsx=pd.ExcelFile("data/Brazilian Immigrants - typo fixed.xlsx")
    df = pd.read_excel(xlsx, year, header=None)
    df.columns = df.iloc[0]
    df.rename(columns=column_dict,inplace=True)
    # for 2014 data, have to do rename columns like this
    c = df.columns.tolist()
    c[0] = 'Type'
    c[1] = 'Class'
    df.columns = c
    df.iloc[0] = df.columns
    return df

read_year('2014').head()


Type         Class   AL   AK    AZ   AR     CA    CO     CT   DE  \
0        Type         Class   AL   AK    AZ   AR     CA    CO     CT   DE   
1  Population    Population  941  123  3075  644  32597  2117  13785  121   
2         Age    Age 0 to 4    0    0     0    0    103     0      0    0   
3         Age  Age 05 to 09    0    0     0    0      0     0      0    0   
4         Age  Age 10 to 19   20    0   451    0   1114     0    545   65   

   ...    SC   SD    TN     TX    UT    VA    WA   WV    WI  WY  
0  ...    SC   SD    TN     TX    UT    VA    WA   WV    WI  WY  
1  ...  2384  255  2519  14635  2562  4046  2094  343  1218  98  
2  ...     0    0   102      0     0     0     0    0     0   0  
3  ...    84    0   104    605    79     0     0    0     0   0  
4  ...    99    0   654    329   450     0   111    0     0  22  

[5 rows x 51 columns]

In [5]:
df2005=read_year('2005')
df2006=read_year('2006')
df2007=read_year('2007')
df2008=read_year('2008')
df2009=read_year('2009')
df2010=read_year('2010')
df2011=read_year('2011')
df2012=read_year('2012')
df2013=read_year('2013')
df2014=read_year('2014')
df2015=read_year('2015')
df2016=read_year('2016')
df2017=read_year('2017')
df2018=read_year('2018')
df2019=read_year('2019')

data_dict={2005:df2005,2006:df2006,2007:df2007,2008:df2008,2009:df2009,2010:df2010,2011:df2011,2012:df2012,2013:df2013,2014:df2014,2015:df2015,2016:df2016,2017:df2017,2018:df2018,2019:df2019}

# data_dict[2005].head(10)

In [6]:
temp=data_dict[2005].copy()
temp.rename(index=temp["Class"],inplace=True)
# temp.head()

In [7]:
# temp.loc["Age 0 to 4"]
temp.drop(columns=['Type', 'Class'], inplace=True)
temp.sort_values(by='Population', ascending=False,axis=1,inplace=True)
# temp.head(100)

In [8]:
pd.options.mode.chained_assignment = None  # default='warn'

def get_data_by_class(class_:str, year:int, data):
    # df = data_dict[year]
    # df = df[df['Class'] == class_]
    # df.drop(columns=['Type', 'Class'], inplace=True)
    # df.sort_values(by=df.index.tolist()[0], ascending=False,axis=1,inplace=True)
    return data.loc[str(class_)]
    # return df

# get_data_by_class('Population', 2014).head()

In [9]:
def get_type(type_:str, year:int):
    df = data_dict[year]
    df = df[df['Type'] == type_]
    return df[['Type', 'Class']]

get_type('Population', 2014).head()

Type       Class
1  Population  Population

In [10]:
from pyecharts import options as opts
from pyecharts.charts import Bar, Timeline
from pyecharts.commons.utils import JsCode
from pyecharts.globals import ThemeType

def plot_bar_by_type(type_:str, save_name:str, stack=False, sort_index='') -> Timeline:
    tl = Timeline(
        init_opts=opts.InitOpts(
            width='800px',
    ))
    tl.add_schema(pos_right= "0px",pos_bottom= "5px",orient = "vertical",width= "75px",height="375px")
        
   
    for year in range(2005, 2020):
        print("processed: "+str(year))
        data = data_dict[year].copy()
        data = data[data['Type'] == type_]
        
        # rename index to Class
        data.rename(index=data["Class"],inplace=True)
        # drop Type and Class
        data.drop(columns=['Type', 'Class'], inplace=True)

        age_class = get_type(type_, year)['Class']
        
        # sort data desc
        if len(sort_index) > 0:
            data.sort_values(by=sort_index, ascending=False,axis=1,inplace=True)
   
        bar = (
            Bar()
            # .add_xaxis(data.columns.tolist()[2:])
            .add_xaxis(data.columns.tolist())
            # .add_yaxis("Population", population.iloc[0].tolist(),
            #     bar_min_width='10px')
            .set_global_opts(
                title_opts=opts.TitleOpts("{}. Year: {}, Sorted by \"{}\"".format(type_, year,sort_index)),
                # xaxis_opts=opts.AxisOpts(type_="category"),
                datazoom_opts=[opts.DataZoomOpts(), opts.DataZoomOpts(type_="inside")],
                legend_opts=opts.LegendOpts(is_show=True,pos_left='40%',pos_top='5%' ),
            )
            
        )

        for class_ in age_class:
#             print(class_)
            if stack:
                bar.add_yaxis(class_, get_data_by_class(class_, year,data).tolist(), stack="stack1")
                # bar.add_yaxis(class_, get_data_by_class(class_, year,data).iloc[0].tolist(), stack="stack1")
            else:
#                 data=get_data_by_class(class_, year,data)
                
                temp=data.loc[class_]
                # data.sort_values(by=1, ascending=False,axis=1,inplace=True)
                bar.add_yaxis(class_, temp.tolist())
                # bar.add_yaxis(class_, data.iloc[0].tolist())

        tl.add(bar, "Year:{}".format(year))

    tl.render("year/" + save_name)
    bar.render_notebook()
    return tl



In [11]:
plot_bar_by_type('Population', 'population.html', sort_index='Population').render_notebook()
# tl.render_notebook()

processed: 2005
processed: 2006
processed: 2007
processed: 2008
processed: 2009
processed: 2010
processed: 2011
processed: 2012
processed: 2013
processed: 2014
processed: 2015
processed: 2016
processed: 2017
processed: 2018
processed: 2019


In [12]:
plot_bar_by_type('Age', 'age.html',sort_index='Age 20 to 24').render_notebook()

processed: 2005
processed: 2006
processed: 2007
processed: 2008
processed: 2009
processed: 2010
processed: 2011
processed: 2012
processed: 2013
processed: 2014
processed: 2015
processed: 2016
processed: 2017
processed: 2018
processed: 2019


In [13]:
plot_bar_by_type('Age', 'age2.html', True,sort_index='Age 20 to 24').render_notebook()

processed: 2005
processed: 2006
processed: 2007
processed: 2008
processed: 2009
processed: 2010
processed: 2011
processed: 2012
processed: 2013
processed: 2014
processed: 2015
processed: 2016
processed: 2017
processed: 2018
processed: 2019


In [14]:
plot_bar_by_type('Gender Distribution', 'gender.html',sort_index='Male').render_notebook()

processed: 2005
processed: 2006
processed: 2007
processed: 2008
processed: 2009
processed: 2010
processed: 2011
processed: 2012
processed: 2013
processed: 2014
processed: 2015
processed: 2016
processed: 2017
processed: 2018
processed: 2019


In [15]:
plot_bar_by_type('Marital Status', 'marital.html',sort_index='Married').render_notebook()

processed: 2005
processed: 2006
processed: 2007
processed: 2008
processed: 2009
processed: 2010
processed: 2011
processed: 2012
processed: 2013
processed: 2014
processed: 2015
processed: 2016
processed: 2017
processed: 2018
processed: 2019


In [16]:
plot_bar_by_type('Citizenship', 'marital.html',sort_index='U.S. citizen by naturalization').render_notebook()

processed: 2005
processed: 2006
processed: 2007
processed: 2008
processed: 2009
processed: 2010
processed: 2011
processed: 2012
processed: 2013
processed: 2014
processed: 2015
processed: 2016
processed: 2017
processed: 2018
processed: 2019


In [17]:
plot_bar_by_type('Year of Entry', 'year_of_entry.html',sort_index='Entered US before 2000').render_notebook()

processed: 2005
processed: 2006
processed: 2007
processed: 2008
processed: 2009
processed: 2010
processed: 2011
processed: 2012
processed: 2013
processed: 2014
processed: 2015
processed: 2016
processed: 2017
processed: 2018
processed: 2019


In [18]:
plot_bar_by_type('Ability to speak English', 'Ability_to_speak_English.html',sort_index='Speaks English Less Than Very Well').render_notebook()

processed: 2005
processed: 2006
processed: 2007
processed: 2008
processed: 2009
processed: 2010
processed: 2011
processed: 2012
processed: 2013
processed: 2014
processed: 2015
processed: 2016
processed: 2017
processed: 2018
processed: 2019


In [19]:
plot_bar_by_type('Educational Attainment of population aged 25 or over', 'Educational_above_25.html',sort_index='Bachelors Degree or Higher').render_notebook()

processed: 2005
processed: 2006
processed: 2007
processed: 2008
processed: 2009
processed: 2010
processed: 2011
processed: 2012
processed: 2013
processed: 2014
processed: 2015
processed: 2016
processed: 2017
processed: 2018
processed: 2019


In [20]:
plot_bar_by_type('Labor Force by Gender', 'labor_force_by_gender.html',sort_index='Males In Civilian Labor Force').render_notebook()

processed: 2005
processed: 2006
processed: 2007
processed: 2008
processed: 2009
processed: 2010
processed: 2011
processed: 2012
processed: 2013
processed: 2014
processed: 2015
processed: 2016
processed: 2017
processed: 2018
processed: 2019


In [21]:
plot_bar_by_type('Unemployment by Gender', 'Unemployment_by_Gender.html',sort_index='Unemployed Males').render_notebook()

processed: 2005
processed: 2006
processed: 2007
processed: 2008
processed: 2009
processed: 2010
processed: 2011
processed: 2012
processed: 2013
processed: 2014
processed: 2015
processed: 2016
processed: 2017
processed: 2018
processed: 2019


In [22]:
plot_bar_by_type('Employment Type', 'Employment_Type.html',sort_index='Private Wage and Salary Workers').render_notebook()

processed: 2005
processed: 2006
processed: 2007
processed: 2008
processed: 2009
processed: 2010
processed: 2011
processed: 2012
processed: 2013
processed: 2014
processed: 2015
processed: 2016
processed: 2017
processed: 2018
processed: 2019


In [23]:
plot_bar_by_type('Employment by Industry', 'Employment_by_Industry.html',sort_index='Education').render_notebook()

processed: 2005
processed: 2006
processed: 2007
processed: 2008
processed: 2009
processed: 2010
processed: 2011
processed: 2012
processed: 2013
processed: 2014
processed: 2015
processed: 2016
processed: 2017
processed: 2018
processed: 2019


In [24]:
plot_bar_by_type('Employment by Occupation', 'Employment_by_Occupation.html',sort_index='Services').render_notebook()

processed: 2005
processed: 2006
processed: 2007
processed: 2008
processed: 2009
processed: 2010
processed: 2011
processed: 2012
processed: 2013
processed: 2014
processed: 2015
processed: 2016
processed: 2017
processed: 2018
processed: 2019


In [25]:
temp=data_dict[2010].copy()
temp.rename(index=temp["Class"],inplace=True)

temp.drop(columns=['Type', 'Class'], inplace=True)
temp_class = get_type('Employment by Occupation', 2011)['Class']
# temp_class.head(10)

In [26]:
# temp.loc['Services'].tolist()

In [27]:
plot_bar_by_type('Poverty Status', 'Poverty_Status.html',sort_index='Individuals Above Poverty').render_notebook()

processed: 2005
processed: 2006
processed: 2007
processed: 2008
processed: 2009
processed: 2010
processed: 2011
processed: 2012
processed: 2013
processed: 2014
processed: 2015
processed: 2016
processed: 2017
processed: 2018
processed: 2019


In [28]:
plot_bar_by_type('Median Personal Earnings', 'Median_Personal_Earnings.html',sort_index='Median Personal Earnings').render_notebook()

processed: 2005
processed: 2006
processed: 2007
processed: 2008
processed: 2009
processed: 2010
processed: 2011
processed: 2012
processed: 2013
processed: 2014
processed: 2015
processed: 2016
processed: 2017
processed: 2018
processed: 2019
